In [23]:
from DATA225utils import make_connection, dataframe_query
import pandas as pd
from pandas import DataFrame

# ZAGI Sales

In [24]:
conn = make_connection(config_file = 'ZAGI-Sales.ini')
cursor = conn.cursor()

## Inner join

In [25]:
_, df = dataframe_query(conn,
    """
    SELECT t.tid, t.tdate, p.product_name,
           sv.no_of_items AS quantity,
           (sv.no_of_items * p.product_price) AS amount
    FROM   product AS p, sales_transaction AS t, sold_via AS sv
    WHERE  sv.product_id = p.product_id 
    AND    sv.tid = t.tid
    ORDER  BY t.tid
    """
                       )

df

tid       tdate product_name  quantity  amount
0  T111  2023-01-23      Zzz Bag         1  100.00
1  T222  2023-02-06    Easy Boot         1   70.00
2  T333  2023-03-14      Zzz Bag         1  100.00
3  T333  2023-03-14    Cosy Sock         5   75.00
4  T444  2023-04-17    Easy Boot         2  140.00
5  T444  2023-04-17    Dura Boot         1   90.00
6  T555  2023-05-01    Dura Boot         4  360.00
7  T555  2023-05-01    Tiny Tent         2  300.00
8  T555  2023-05-01   Biggy Tent         1  250.00

## Inner join (alternate syntax)

In [26]:
_, df = dataframe_query(conn,
    """
    SELECT t.tid, t.tdate, p.product_name,
           sv.no_of_items AS quantity,
           (sv.no_of_items * p.product_price) AS amount
    FROM product AS p
    JOIN sold_via AS sv ON p.product_id = sv.product_id
    JOIN sales_transaction AS t ON t.tid = sv.tid
    ORDER  BY t.tid    
    """
                       )

df

tid       tdate product_name  quantity  amount
0  T111  2023-01-23      Zzz Bag         1  100.00
1  T222  2023-02-06    Easy Boot         1   70.00
2  T333  2023-03-14      Zzz Bag         1  100.00
3  T333  2023-03-14    Cosy Sock         5   75.00
4  T444  2023-04-17    Easy Boot         2  140.00
5  T444  2023-04-17    Dura Boot         1   90.00
6  T555  2023-05-01    Dura Boot         4  360.00
7  T555  2023-05-01    Tiny Tent         2  300.00
8  T555  2023-05-01   Biggy Tent         1  250.00

In [27]:
cursor.close()
conn.close()

# Building

In [28]:
conn = make_connection(config_file = 'building.ini')
cursor = conn.cursor()

## Self join

In [29]:
_, df = dataframe_query(conn,
    """
    SELECT c.ccname AS client, r.ccname AS recommender
    FROM   corpclient c, corpclient r
    WHERE  r.ccid = c.ccidreferredby    
    """
                       )

df

client recommender
0     SkyJet  BlingNotes
1    WindyCT      SkyJet
2  SouthAlps     WindyCT

## Left outer join

In [30]:
_, df = dataframe_query(conn,
    """
    SELECT a.buildingid, a.aptno, c.ccname
    FROM apartment a 
    LEFT OUTER JOIN corpclient c ON a.ccid = c.ccid
    ORDER BY a.buildingid, a.aptno
    """
                       )

df

buildingid aptno      ccname
0         B1    21  BlingNotes
1         B1    41        None
2         B2    11      SkyJet
3         B2    31        None
4         B3    11     WindyCT
5         B4    11     WindyCT

## Right outer join

In [31]:
_, df = dataframe_query(conn,
    """
    SELECT a.buildingid, a.aptno, c.ccname
    FROM apartment a 
    RIGHT OUTER JOIN corpclient c ON a.ccid = c.ccid
    ORDER BY a.buildingid, a.aptno
    """
                       )

df

buildingid aptno      ccname
0       None  None   SouthAlps
1         B1    21  BlingNotes
2         B2    11      SkyJet
3         B3    11     WindyCT
4         B4    11     WindyCT

## Full outer join (MySQL)

In [32]:
_, df = dataframe_query(conn,
    """
    SELECT a.buildingid, a.aptno, c.ccname
    FROM apartment a 
    LEFT OUTER JOIN corpclient c ON a.ccid = c.ccid
    UNION
    SELECT a.buildingid, a.aptno, c.ccname
    FROM apartment a 
    RIGHT OUTER JOIN corpclient c ON a.ccid = c.ccid
    """
                       )

df

buildingid aptno      ccname
0         B1    41        None
1         B2    31        None
2         B1    21  BlingNotes
3         B2    11      SkyJet
4         B3    11     WindyCT
5         B4    11     WindyCT
6       None  None   SouthAlps

In [33]:
cursor.close()
conn.close()